In [1]:
import numpy as np
import pandas as pd
import re
import glob #this makes a list of all the files in a directory
from pandasql import sqldf
pysqldf = lambda q: sqldf(q, globals())
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.utils import shuffle
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import BernoulliNB
from sklearn.metrics import confusion_matrix
from sklearn import metrics
from sklearn.metrics import classification_report
from sklearn.feature_extraction.text import *

In [2]:
with_gender = pd.read_pickle("WithGenderFinal.p")
with_gender['gender'].value_counts()
line_column=[]
for i in with_gender.index:
        line_column.append(' '.join(with_gender['Speech'][i]))
with_gender['Line']=line_column

with_gender['linelength']=with_gender['Line'].str.len()
with_gender_dum = pd.get_dummies(with_gender['gender'])
with_gender = pd.concat([with_gender, with_gender_dum],axis=1).drop(['F','gender'],1)

In [7]:
with_gender['M'].value_counts()

1    201934
0     84804
Name: M, dtype: int64

In [10]:
print "Most Common Class (Baseline) Accuracy:", round(100*(201934.0/(201934+84804)),2)

Most Common Class (Baseline) Accuracy: 70.42


In [5]:
#didn't end up using the word2vec
#import gensim

In [4]:
#didn't need to split the words if not vectorizing
#with_gender['words']=with_gender['Line'].str.split()
#with_gender.head()

In [7]:
#model = gensim.models.Word2Vec(with_gender['words'], min_count=1)
#we already trained this, just load it below

In [8]:
#model.save('trainedwords')

In [36]:
#model = gensim.models.Word2Vec.load('trainedwords')

In [16]:
#word_vectors = model.wv
#del model

In [5]:
#vec_column = []
#for i in with_gender.index:
#    word_vecs=[]
#    for j in with_gender['words'][i]:
#        word_vecs.append(word_vectors[j])
#    vec_column.append(word_vecs)
#with_gender['wordvecs']=vec_column
#with_gender.head()

In [2]:
#vectorized = with_gender
#vectorized.to_pickle('vectorized_lines.p')
#vectorized=pd.read_pickle('vectorized_lines.p')

In [11]:
with_gender_shuffle = shuffle(with_gender, random_state = 5)


# Randomly split into training and dev with scikit-learn helper function
train, test = train_test_split(with_gender_shuffle, test_size=0.2, random_state=100)
dev, test = train_test_split(test, test_size=0.5, random_state=200)

print train.shape
print dev.shape
print test.shape

(229390, 9)
(28674, 9)
(28674, 9)


In [12]:
train.head(n=2)

Char         Title    Genre                pkey  LineID  \
96935     BEN     knockedup  Romance       ben-knockedup     364   
177393  JIMMY  jimmyandjudy   Action  jimmy-jimmyandjudy     267   

                                       Speech  \
96935                                 [Okay.]   
177393  [Be normal.     Be normal.   Be norm]   

                                       Line  linelength  M  
96935                                 Okay.           5  1  
177393  Be normal.     Be normal.   Be norm          35  1

In [13]:
train_y, dev_y, test_y = train.M, dev.M, test.M
train_X = train.drop(['M','Speech','LineID','pkey','linelength'],1)
dev_X = dev.drop(['M','Speech','LineID','pkey','linelength'],1)
test_X = test.drop(['M','Speech','LineID','pkey','linelength'],1)
dev_X.head()

Char         Title    Genre  \
151043      GARY     antitrust    Crime   
62727      NADIA  birthdaygirl    Crime   
203327     MARTY         marty  Romance   
39225   JENNIFER       scream3  Mystery   
102806     BLOOM   producerthe   Comedy   

                                                     Line  
151043  The purpose of this company isn't to destroy o...  
62727                I know you just want to punish me --  
203327  I like you. I like you. I been telling you all...  
39225                              Sidney, what happened?  
102806               I never should have listened to you.

In [14]:
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten
from keras.layers import Conv1D, GlobalMaxPooling1D
from keras.utils import np_utils
from keras.layers import Embedding
from keras.preprocessing import sequence

Using TensorFlow backend.


In [15]:
NUM_WORDS=20000
from keras.preprocessing.text import Tokenizer
t=Tokenizer(num_words=NUM_WORDS, 
            filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n\'', 
            lower=True)

t.fit_on_texts(train_X.Line.values)

x_train = t.texts_to_sequences(train_X.Line.values)
x_test = t.texts_to_sequences(test_X.Line.values)
x_dev = t.texts_to_sequences(dev_X.Line.values)

In [16]:
print train_X.Line.values[1]
print x_train[1]

print train_X.Line.values[2]
print x_train[2]

print dev_X.Line.values[1]
print x_dev[1]

print dev_X.Line.values[2]
print x_dev[2]

Be normal.     Be normal.   Be norm
[30, 1225, 30, 1225, 30, 7276]
He was... the kind of person I thought I wanted to be.
[16, 33, 3, 225, 11, 502, 2, 167, 2, 251, 4, 30]
I know you just want to punish me --
[2, 28, 1, 38, 59, 4, 7633, 15]
I like you. I like you. I been telling you all night, I like you...
[2, 41, 1, 2, 41, 1, 2, 92, 536, 1, 39, 132, 2, 41, 1]


In [17]:
maxlen=500
print('Pad sequences (samples x time)')
x_train = sequence.pad_sequences(x_train, maxlen=maxlen)
x_test = sequence.pad_sequences(x_test, maxlen=maxlen)
x_dev = sequence.pad_sequences(x_dev, maxlen=maxlen)
print('x_train shape:', x_train.shape)
print('x_test shape:', x_test.shape)
print('x_dev shape:', x_dev.shape)

Pad sequences (samples x time)
('x_train shape:', (229390, 500))
('x_test shape:', (28674, 500))
('x_dev shape:', (28674, 500))


In [21]:
labels= train_y.values.reshape(-1,1)
labels_dev=dev_y.values.reshape(-1,1)
labels_test = test_y.values.reshape(-1,1)
print('labels shape:', labels.shape)
print('labels_test shape:', labels_test.shape)
print('labels_dev shape:', labels_dev.shape)

('labels shape:', (229390, 1))
('labels_test shape:', (28674, 1))
('labels_dev shape:', (28674, 1))


In [ ]:
cnn_model = Sequential()
    
max_features=10000
embedding_dims=100

cnn_model.add(Embedding(max_features,
                    embedding_dims,
                    input_length=maxlen))
cnn_model.add(Dropout(0.2))

cnn_model.add(Conv1D(10, 3, 
                     padding='valid', 
                     activation='relu',
                     strides=1,
                     input_shape=train.shape))

cnn_model.add(GlobalMaxPooling1D())
cnn_model.add(Dropout(0.25))
cnn_model.add(Activation('relu'))
cnn_model.add(Dense(1))
          
cnn_model.add(Activation('sigmoid'))

cnn_model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
          
cnn_model.fit(x_train, labels,
          batch_size=32,
          epochs=4,
          validation_data=(x_dev, labels_dev))

Train on 215353 samples, validate on 26919 samples
Epoch 1/4
215353/215353 [==============================] - 297s 1ms/step - loss: 0.6107 - acc: 0.6949 - val_loss: 0.5954 - val_acc: 0.6995

In [27]:
#to get the word embeddings run in terminal:
#wget -O 'PretrainedWord2Vec.bin.gz' "https://s3.amazonaws.com/dl4j-distribution/GoogleNews-vectors-negative300.bin.gz"
#gunzip PretrainedWord2Vec.bin.gz

import gensim
from gensim.models import Word2Vec
from gensim.utils import simple_preprocess

from gensim.models.keyedvectors import KeyedVectors

word_vectors = KeyedVectors.load_word2vec_format('PretrainedWord2Vec.bin', binary=True)

In [28]:
word_index = t.word_index
EMBEDDING_DIM=300
vocabulary_size=min(len(word_index)+1,NUM_WORDS)
embedding_matrix = np.zeros((vocabulary_size, EMBEDDING_DIM))
for word, i in word_index.items():
    if i>=NUM_WORDS:
        continue
    try:
        embedding_vector = word_vectors[word]
        embedding_matrix[i] = embedding_vector
    except KeyError:
        embedding_matrix[i]=np.random.normal(0,np.sqrt(0.25),EMBEDDING_DIM)

del(word_vectors)

from keras.layers import Embedding
embedding_layer = Embedding(vocabulary_size,
                            EMBEDDING_DIM,
                            weights=[embedding_matrix],
                            trainable=True)

In [30]:
cnn_model = Sequential()

#Uses pretrained word embeddings:
cnn_model.add(embedding_layer)

cnn_model.add(Dropout(0.2))

cnn_model.add(Conv1D(10, 3, 
                     padding='valid', 
                     activation='relu',
                     strides=1,
                     input_shape=train.shape))

cnn_model.add(GlobalMaxPooling1D())
cnn_model.add(Dropout(0.25))
cnn_model.add(Activation('relu'))
cnn_model.add(Dense(1))
          
cnn_model.add(Activation('sigmoid'))

cnn_model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
          
cnn_model.fit(x_train, labels,
          batch_size=32,
          epochs=2,
          validation_data=(x_dev, labels_dev))

Train on 229390 samples, validate on 28674 samples
Epoch 1/2
229390/229390 [==============================] - 801s 3ms/step - loss: 0.5921 - acc: 0.7058 - val_loss: 0.5751 - val_acc: 0.7142

In [33]:
cnn_model = Sequential()

#Uses pretrained word embeddings:
cnn_model.add(embedding_layer)

cnn_model.add(Dropout(0.2))

cnn_model.add(Conv1D(10, 5, 
                     padding='valid', 
                     activation='relu',
                     strides=1,
                     input_shape=train.shape))

cnn_model.add(GlobalMaxPooling1D())
cnn_model.add(Dropout(0.25))
cnn_model.add(Activation('relu'))
cnn_model.add(Dense(1))
          
cnn_model.add(Activation('sigmoid'))

cnn_model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
          
cnn_model.fit(x_train, labels,
          batch_size=1000,
          epochs=2,
          validation_data=(x_dev, labels_dev))

Train on 229390 samples, validate on 28674 samples
Epoch 1/2
229390/229390 [==============================] - 781s 3ms/step - loss: 0.5673 - acc: 0.7158 - val_loss: 0.5764 - val_acc: 0.7172

In [34]:
score = cnn_model.evaluate(x_test, labels_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])

('Test loss:', 0.58523509578408162)
('Test accuracy:', 0.71308502476110758)


In [ ]:
cnn_model = Sequential()
    
max_features=10000
embedding_dims=100

cnn_model.add(Embedding(max_features,
                    embedding_dims,
                    input_length=maxlen))
cnn_model.add(Dropout(0.2))

cnn_model.add(Conv1D(10, 5, 
                     padding='valid', 
                     activation='relu',
                     strides=1,
                     input_shape=train.shape))

cnn_model.add(GlobalMaxPooling1D())
cnn_model.add(Dropout(0.25))
cnn_model.add(Activation('relu'))
cnn_model.add(Dense(1))
          
cnn_model.add(Activation('sigmoid'))

cnn_model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
          
cnn_model.fit(x_train, labels,
          batch_size=32,
          epochs=2,
          validation_data=(x_dev, labels_dev))

Train on 215353 samples, validate on 26919 samples
Epoch 1/2
127744/215353 [================>.............] - ETA: 3:34 - loss: 0.6078 - acc: 0.6946 

In [14]:
score = cnn_model.evaluate(x_test, labels_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])

('Test loss:', 0.58311944330252297)
('Test accuracy:', 0.70601783060921253)


In [12]:
cnn_model

In [25]:
cnn_model = Sequential()
    
max_features=20000
embedding_dims=100

cnn_model.add(Embedding(max_features,
                    embedding_dims,
                    input_length=maxlen))
cnn_model.add(Dropout(0.2))

cnn_model.add(Conv1D(10, 3, 
                     padding='valid', 
                     activation='relu',
                     strides=1,
                     input_shape=x_train.shape))

cnn_model.add(GlobalMaxPooling1D())
cnn_model.add(Dropout(0.25))
cnn_model.add(Activation('relu'))
cnn_model.add(Dense(1))
          
cnn_model.add(Activation('tanh'))

cnn_model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
          
cnn_model.fit(x_train, labels,
          batch_size=32,
          epochs=2,
          validation_data=(x_dev, labels_dev))

Train on 229390 samples, validate on 28674 samples
Epoch 1/2
229390/229390 [==============================] - 303s 1ms/step - loss: 0.7546 - acc: 0.6568 - val_loss: 0.6081 - val_acc: 0.7098

In [26]:
score = cnn_model.evaluate(x_test, labels_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])

('Test loss:', 0.58429159373595818)
('Test accuracy:', 0.71318964915951732)


In [ ]:
cnn_model = Sequential()
    
max_features=10000
embedding_dims=100

cnn_model.add(Embedding(max_features,
                    embedding_dims,
                    input_length=maxlen))
cnn_model.add(Dropout(0.2))

cnn_model.add(Conv1D(10, 3, 
                     padding='valid', 
                     activation='relu',
                     strides=1,
                     input_shape=train.shape))

cnn_model.add(GlobalMaxPooling1D())
cnn_model.add(Dropout(0.25))
cnn_model.add(Activation('relu'))
cnn_model.add(Dense(1))
          
cnn_model.add(Activation('sigmoid'))

cnn_model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
          
cnn_model.fit(x_train, labels,
          batch_size=1000,
          epochs=4,
          validation_data=(x_dev, labels_dev))

Train on 215353 samples, validate on 26919 samples
Epoch 1/10
215353/215353 [==============================] - 233s 1ms/step - loss: 0.6132 - acc: 0.6938 - val_loss: 0.6030 - val_acc: 0.6932

In [28]:
score = cnn_model.evaluate(x_test, labels_test)
print('Test loss:', score[0])
print('Test accuracy:', score[1])

26920/26920 [==============================] - 7s 258us/step

In [35]:

confusion_matrix = np.zeros((embedding_dims, embedding_dims))
misclassified = []

In [36]:
predictions = cnn_model.predict_classes(x_test, batch_size=1000)

28674/28674 [==============================] - 21s 734us/step

In [34]:
num_correct = 0
for i in range(0,26920):
    predicted_class = predictions[i]
    correct = np.nonzero(labels_test[i])
    correct = correct[0][0]
    confusion_matrix[correct][predicted_class] += 1
    if predicted_class == correct:
      num_correct += 1
    else:
      # Save the image file name, its correct class, and its predicted class.
      misclassified.append((test_img_files[i], correct, predicted_class))

NameError: name 'test_img_files' is not defined

In [37]:

probabilities = cnn_model.predict(x_test, verbose=1)

28674/28674 [==============================] - 26s 905us/step

In [38]:
probabilities

array([[ 0.84855187],
       [ 0.61104512],
       [ 0.57104707],
       ..., 
       [ 0.98433971],
       [ 0.81841338],
       [ 0.65761673]], dtype=float32)

In [39]:
from sklearn.metrics import confusion_matrix

y_pred = probabilities > 0.5

confusion_matrix(labels_test, y_pred)

array([[ 1524,  6871],
       [ 1356, 18923]])

In [40]:
labels_test

array([[1],
       [1],
       [1],
       ..., 
       [1],
       [0],
       [1]], dtype=uint8)

In [41]:
binarized_pred = probabilities.round()

In [46]:
wrong_probs=[]
print "Correctly Labeled as Female:"
for i in range(len(binarized_pred)):
    if int(binarized_pred[i]) == int(labels_test[i]):
        if int(labels_test[i])==0:
            #print "correct call"
            print test_X.Line.values[i], "\n"
    else:
        #print "Incorrect prediction: called %s instead of %s, %3.4f sure" % (binarized_pred[i], labels_test[i], probabilities[i])
        #print test_X.Line.values[i]
        wrong_probs.append(probabilities[i])

print np.mean(wrong_probs)

Correctly Labeled as Female:
Last night. At my house. You were hurt. You had two black eyes and blood everywhere and... 

(through cigarette) You never tried it, did you? Then you agree I'm smarter than you... 

Mumble, that's just cheap 

Yes. I tried to talk to Ted  my ex- husband  about it, but he wouldn't listen. He refuses to discuss it in any serious way. I remember one time he said I probably couldn't get a job that would pay enough to hire a baby-sitter for Billy. 

(from her gut) I am not! I'm a terrible mother! I'm an awful mother. I yell at him all the time. I have no patience. No... No. He's better off without me. (unable to look at Ted) Ted, I've got to go... I've got to go. 

(offscreen) Isn't this great? (chuckling) They have everything here. 

Thank you. (takes drink) I thought you were avoiding me. 

(whispering) Why did you hate me? 

Why are you home so late? 28. 

It's sex time. 

I'm losing my mind. 

Ooh, I just felt her kick. C'mon, Bernie, gimme your hand... 

I

In [48]:
lengths_inc_female=[]

print "Incorrectly Labeled as Female:"
for i in range(len(binarized_pred)):
    if int(binarized_pred[i]) == int(labels_test[i]):
        pass
    else:
        if int(labels_test[i])==0:
            #print "correct call"
            print test_X.Line.values[i], "\n"
            lengths_inc_female.append(len(test_X.Line.values[i].split()))
print np.mean(lengths_inc_female)

Incorrectly Labeled as Female:
(astonished) What should I do?  Call the cops? 

Hm? Oh, I'm the heiress to a fortune built on small pets. 

Then close your eyes, and tap your heels together three times. 

Shut up dad! 

I want to book a hire car. 

Jim, you've gotta get your spare helmet from storage. 

Okay...okay... 

The concert was lame. The opening act singer ripped his leather pants during a stupid dance routine and stormed off stage. (pause, looks at his cut) Are you okay? 

It starts in a little while. 

Hey... 

My daughter's close to dying. 33. 

The minute we get off this train. 

Really? 

And you brought vermin with you. 

You drink too much. 

I'd have finished by now, but the police wouldn't let me touch anything. They didn't believe it was suicide. 

Mm-hmm. You know, you could pay me. That's one way to maybe break the ice. 

Curtis.  What about you?  Do we understand each other?  You stay put. 

You. You tricked me. 123 

My name is not Zoe.  Not any more. 

Which thin

In [50]:
lengths_inc_male=[]

print "Incorrectly Labeled as Male:"
for i in range(len(binarized_pred)):
    if int(binarized_pred[i]) == int(labels_test[i]):
        pass
    else:
        if int(labels_test[i])==1:
            #print "correct call"
            print test_X.Line.values[i], "\n"
            lengths_inc_male.append(len(test_X.Line.values[i].split()))
print np.mean(lengths_inc_male)

Incorrectly Labeled as Male:
You're calling me a pestilence? That's a hoot! 

You saw the body? 

(cutting him off) Just a second.  Not to be rude, Keith, but I got to ask, are you a cop? 

Goodbye, Pete. 

Oh, thank goodness. 

(softly, but insistently) Please! 

We're in somebody's garden. 

Because she's ashamed. 

I saw my sister. 

Come on. Don't cry. Please. It's all right. It's going to be all right. 

I don't need college, Mr. Fernandez. 

(to the bartender) Marv, let's get Ronnie set up here. 

I like those sapphire earrings myself. 

Hi baby. 

Please to light your candles. 

Come on, honey, let's get out of here. 

Feel like traveling? 

I don't want to say I told you so. But I did. Can I go back to work now? 

Hi ! 

I live in Connecticut. I haven't used it in a long time. 

Jackie, they come to be part of my life.  Rachel part of that life. 

(triumphant smile) Teddy! 

My mother's inside. 

Sam? Sam? 

(inner voice) To avenge my father, I will turn you into killing machin